In [ ]:
from astropy.io import fits
from astropy.coordinates import SkyCoord
from astropy.coordinates import match_coordinates_sky
from astropy import units as u
import numpy as np
from pathlib import Path
import csv

In [ ]:
hsc_dir_name = '/mnt/research/data/DELVE/HSC/'
hsc_files = ['mag_i lt 22.fits',\
             '22 lt mag_i lt 23.5.fits',\
             '23.5 lt mag_i lt 24.5.fits',\
             '24.5 lt mag_i lt 25.fits']

             
pixel_start = 6133 # 5993
pixel_end = 6134 # 7026
delve_dir_name = '/mnt/research/data/DELVE/delve_wide/decade.ncsa.illinois.edu/delve_wide/dr1-old/'

out_dir_name = '/mnt/research/data/DELVE/'
out_file_name = 'HSC_comparison.csv'

In [ ]:
lower_spread_limit = -0.025
upper_spread_limit = 0.045
min_ext = 0.003
wide_ext = 0.005
max_sep = 0.1 * u.arcsec
debug = False

In [ ]:
def set_mag_limits(hsc_file):
  if hsc_file == 'mag_i lt 22.fits':
    lower_limit = -10
    upper_limit = 22
  elif hsc_file == '22 lt mag_i lt 23.5.fits':
    lower_limit = 22
    upper_limit = 23.5
  elif hsc_file == '23.5 lt mag_i lt 24.5.fits':
    lower_limit = 23.5
    upper_limit = 24.5
  elif hsc_file == '24.5 lt mag_i lt 25.fits':
    lower_limit = 24.5
    upper_limit = 25.5
  else:
    lower_limit = -10
    upper_limit = 26
    
  return lower_limit, upper_limit

In [ ]:
def get_pixel_range(delve_fqpn):
  delve_hdul = fits.open(delve_fqpn, memmap=True)
  delve_data = delve_hdul[1].data

  # get range of delve pixel data
  dec_max = np.max(np.array(delve_data['DEC']))
  dec_min = np.min(np.array(delve_data['DEC']))
  RA_max = np.max(np.array(delve_data['RA']))
  RA_min = np.min(np.array(delve_data['RA']))


  delve_hdul.close()
  return dec_max, RA_max, dec_min, RA_min

In [ ]:
def delve_setup(delve_fqpn):
  delve_hdul = fits.open(delve_fqpn, memmap=True)
  delve_data = delve_hdul[1].data
  if debug == True:
    print('Initial delve data size: ', len(delve_data))

  # select objects in delve data in appropriate magnitude and spread model range
  delve_indices = (delve_data['MAG_AUTO_G'] > lower_mag_limit) & (delve_data['MAG_AUTO_G'] < upper_mag_limit) \
                & (delve_data['SPREAD_MODEL_G'] > lower_spread_limit) & (delve_data['SPREAD_MODEL_G'] < upper_spread_limit)
  if debug == True:
    print('Delve data size in magnitude and spread limits: ',len(delve_data[delve_indices]))
   
  # select probable galaxies in delve data
  three_sigma_extension = ((delve_data['SPREAD_MODEL_G'][delve_indices]) + 3*(delve_data['SPREADERR_MODEL_G'][delve_indices])) > wide_ext
  one_sigma_extension = ((delve_data['SPREAD_MODEL_G'][delve_indices]) + (delve_data['SPREADERR_MODEL_G'][delve_indices])) > min_ext
  bigger_than_PSF = ((delve_data['SPREAD_MODEL_G'][delve_indices]) - (delve_data['SPREADERR_MODEL_G'][delve_indices])) > min_ext
  extended_class = three_sigma_extension.astype(np.int16) + one_sigma_extension.astype(np.int16) + bigger_than_PSF.astype(np.int16)

  galaxy_decs = delve_data['DEC'][delve_indices][extended_class > 1]
  galaxy_ras = delve_data['RA'][delve_indices][extended_class > 1]
  if debug == True:
    print('Delve galaxy count: ', len(galaxy_decs))

  # Set up coordinate tree for comparison with HSC data
  delve_ds = SkyCoord(ra=galaxy_ras*u.degree, dec=galaxy_decs*u.degree)

  delve_hdul.close()
  return delve_ds

In [ ]:
def hsc_setup(hsc_fqpn):
  hsc_hdul = fits.open(hsc_fqpn, memmap=True)
  hsc_data = hsc_hdul[1].data
  if debug == True:
    print ('Initial hsc data size: ', len(hsc_data))
    
  # Limit HSC data to area of Delve pixel
  hsc_indices = (hsc_data['ra'] > min_RA) & (hsc_data['ra'] < max_RA) \
              & (hsc_data['dec'] > min_dec) & (hsc_data['dec'] < max_dec)
  hsc_ras = hsc_data['ra'][hsc_indices]
  hsc_decs = hsc_data['dec'][hsc_indices]
  if debug == True:
    print('HSC data size in area of interest: ', len(hsc_ras))

  # Set up coordinate array for match comparison
  hsc_ds = SkyCoord(ra=hsc_ras*u.degree, dec=hsc_decs*u.degree)

  hsc_hdul.close()
  return hsc_ds 

In [ ]:
def calc_matches(delve_ds, hsc_ds):
  low_limit = '(' + str(min_dec) + ',' + str(min_RA) + ')'
  upper_limit = '(' + str(max_dec) + ',' + str(max_RA) + ')'
  if (len(delve_ds) > 0) & (len(hsc_ds) > 0):
    idx, d2d, d3d = match_coordinates_sky(delve_ds, hsc_ds)
    sep_constraint = d2d < max_sep
    hsc_matches = hsc_ds[idx[sep_constraint]]
    fraction = len(hsc_matches) / len(delve_ds)
  else:
    fraction = 0.0
  if debug == True:
    print(f'Fraction of delve galaxies in the range (%7.3f,%7.3f) and (%7.3f,%7.3f) that are also in the hsc catalog between magnitudes {lower_mag_limit} and {upper_mag_limit}: %6.4f'\
          % (min_dec, min_RA, max_dec, max_RA, len(hsc_matches)/len(delve_ds)))
  results_writer.writerow([pixel, low_limit, upper_limit, str(lower_mag_limit), str(upper_mag_limit), fraction])

In [ ]:
pixel = pixel_start

# set up output file
out_fqpn = out_dir_name + out_file_name
results_file = open(out_fqpn, mode='w')
results_writer = csv.writer(results_file, delimiter=';', quotechar='"', quoting=csv.QUOTE_MINIMAL)
results_writer.writerow(["pixel", "min coord", "max coord", "lower mag limit", "upper mag limit", "percentage"])

while pixel < pixel_end:
  delve_fqpn = delve_dir_name + 'cat_hpx_0' + str(pixel) +'.fits'
  delve_check = Path(delve_fqpn)
  if delve_check.is_file():
    max_dec, max_RA, min_dec, min_RA = get_pixel_range(delve_fqpn)
    for hsc_file_name in hsc_files:
      hsc_fqpn = hsc_dir_name + hsc_file_name
      lower_mag_limit, upper_mag_limit = set_mag_limits(hsc_file_name)
      delve = delve_setup(delve_fqpn)
      hsc = hsc_setup(hsc_fqpn)
      calc_matches(delve, hsc)
      del delve, hsc
  pixel += 1
results_file.close()
